# Track/Segment Recycling Object with SiamMask

## Install important components for SiamMask

In [1]:
# Getting python libraries
import os
from os.path import exists, join, basename, splitext
from os import listdir
from os.path import isfile, join
import sys
import time
import matplotlib
import matplotlib.pyplot as plt
plt.rcParams["axes.grid"] = False
import io
import base64
from IPython.display import HTML


from IPython.display import YouTubeVideo

import cv2
import torchvision
import cv2
import numpy as np
import torch
torch.set_grad_enabled(False)

# Cloning SiamMask repo and installing all dependencies needed to run
git_repo_url = 'https://github.com/foolwood/SiamMask.git'
tracker_name = splitext(basename(git_repo_url))[0]
if not exists(tracker_name):
  # clone and install dependencies
  !git clone -q --depth 1 {git_repo_url}
  !sed -i "/torch/d" {tracker_name}/requirements.txt
  !cd {tracker_name} && pip install -q -r requirements.txt
  !cd {tracker_name} && bash make.sh

# Getting correct path of needed information
sys.path.append(tracker_name)
sys.path.append(join(tracker_name, 'experiments', 'siammask_sharp'))
from types import SimpleNamespace
from custom import Custom
from tools.test import *

     |████████████████████████████████| 2.1MB 11.6MB/s 
     |████████████████████████████████| 13.9MB 229kB/s 
     |████████████████████████████████| 61kB 318kB/s 
     |████████████████████████████████| 12.6MB 53.2MB/s 
     |████████████████████████████████| 1.9MB 49.9MB/s 
     |████████████████████████████████| 31.2MB 100kB/s 
     |████████████████████████████████| 2.8MB 51.2MB/s 
     |████████████████████████████████| 8.8MB 50.7MB/s 
     |████████████████████████████████| 51kB 8.9MB/s 
     |████████████████████████████████| 133kB 55.7MB/s 
     |████████████████████████████████| 25.0MB 1.3MB/s 
     |████████████████████████████████| 61kB 10.7MB/s 
ERROR: xarray 0.15.1 has requirement pandas>=0.25, but you'll have pandas 0.23.4 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement h5py~=2.10.0, but you'll have h5py 2.8.0 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement numpy~=1.19.2, but you'll have numpy 1.15.4 which is incompatible.
ERROR: spacy 2.2.

### Connect Google Colab to Google Drive for video extraction

In [2]:
from google.colab import drive
drive.mount('/content/drive')


##### Change files accordingly ###############
# We are taking input video from Google Drive. Fix paths accordingly
inputVideo = '/content/drive/Shareddrives/CS585 Final Project/recycling_tracking_data/input.mp4'
dataPath = '/content/drive/Shareddrives/CS585 Final Project/recycling_tracking_data/'
segmentedImagePath = '/content/drive/Shareddrives/CS585 Final Project/recycling_tracking_data/frame_000030.png'

Mounted at /content/drive


## Download pretrained weights and initialize SiamMask 

## Loading in SiamMASK DAVIS pretrained weights

In [3]:
# Loading the DAVIS weights to begin training from
exp_path = 'SiamMask/experiments/siammask_sharp'
pretrained_path = join(exp_path, 'SiamMask_DAVIS.pth')

# Download pretrained DAVID weights from site
if not exists(pretrained_path):
  !cd {exp_path} && wget http://www.robots.ox.ac.uk/~qwang/SiamMask_DAVIS.pth
    
# init SiamMask for Google Colab GPU use
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
cfg = load_config(SimpleNamespace(config=join(exp_path, 'config_davis.json')))
siammask = Custom(anchors=cfg['anchors'])

# Use siamMask to run builtin functions
siammask = load_pretrain(siammask, pretrained_path)
siammask = siammask.eval().to(device)

--2021-04-27 23:57:56--  http://www.robots.ox.ac.uk/~qwang/SiamMask_DAVIS.pth
Resolving www.robots.ox.ac.uk (www.robots.ox.ac.uk)... 129.67.94.2
Connecting to www.robots.ox.ac.uk (www.robots.ox.ac.uk)|129.67.94.2|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://www.robots.ox.ac.uk/~qwang/SiamMask_DAVIS.pth [following]
--2021-04-27 23:57:57--  https://www.robots.ox.ac.uk/~qwang/SiamMask_DAVIS.pth
Connecting to www.robots.ox.ac.uk (www.robots.ox.ac.uk)|129.67.94.2|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 105878246 (101M)
Saving to: ‘SiamMask_DAVIS.pth’

SiamMask_DAVIS.pth  100%[===================>] 100.97M  22.5MB/s    in 5.3s    

2021-04-27 23:58:03 (18.9 MB/s) - ‘SiamMask_DAVIS.pth’ saved [105878246/105878246]



[2021-04-27 23:58:03,798-rk0-features.py# 66] Current training 0 layers:
	
[2021-04-27 23:58:03,800-rk0-features.py# 66] Current training 1 layers:
	
[2021-04-27 23:58:03,874-rk0-load_helper.py# 31] load pretrained model from SiamMask/experiments/siammask_sharp/SiamMask_DAVIS.pth
[2021-04-27 23:58:14,686-rk0-load_helper.py# 25] remove prefix 'module.'
[2021-04-27 23:58:14,691-rk0-load_helper.py# 18] used keys:356


## Track a person on a test video with SiamMask

We will replace this with the recycling tracking video

In [4]:
# Recycling video for testing
# The input video was made by connecting all frames from the recyling dataset in order of occurance
idx = 0
video_test = cv2.VideoCapture()
if video_test.open(inputVideo):
  width, height = int(video_test.get(cv2.CAP_PROP_FRAME_WIDTH)), int(video_test.get(cv2.CAP_PROP_FRAME_HEIGHT))
  fps = video_test.get(cv2.CAP_PROP_FPS)
  fps = 30

  !rm -f output.mp4 output.avi
  
  # Writing to an AVI file
  video_writer = cv2.VideoWriter("outputVideo.avi", cv2.VideoWriter_fourcc(*'MJPG'), fps, (width, height))
  
  while video_test.isOpened():
    ret, frame = video_test.read()
    if not ret:
      break

    if idx == 0:

      # First thing we do is
      # Get the first frame (segmented) and determine the centroid of the object (top left corner of the screen for recycling data
      # Use OpenCV to threshold the image and find the contours of the image (Should only be one)
      imgAnn = cv2.imread(segmentedImagePath)
      imgAnn = cv2.cvtColor(imgAnn, cv2.COLOR_BGR2GRAY)
      _, thres_output = cv2.threshold(imgAnn, 7, 255, 0)

      # Depending on OpenCV version 
      # Run this if issue occurs
      # _, contours, hierarchy = cv2.findContours(thres_output, cv2.RETR_EXTERNAL , cv2.CHAIN_APPROX_SIMPLE)
      contours, hierarchy = cv2.findContours(thres_output, cv2.RETR_EXTERNAL , cv2.CHAIN_APPROX_SIMPLE)

      # Find the x coordinate, y coordinate, height and width of the box around the object
      boundrec = cv2.boundingRect(contours[0])
      x = boundrec[0]
      y = boundrec[1]
      w = boundrec[2]
      h = boundrec[3]
      target_pos = np.array([x + w / 2, y + h / 2])
      target_sz = np.array([w, h])

      # initialize tracker using siamese_init function available on the testing.py file in SiamMask repo
      state = siamese_init(frame, target_pos, target_sz, siammask, cfg['hp'], device=device)
    else:
      # After initializing the tracker, maintain the same object using siamese_track on test.py
      state = siamese_track(state, frame, mask_enable=True, refine_enable=True, device=device)

      # Apply red mask around object during process of video for visual purposes
      mask = state['mask'] > state['p'].seg_thr
      frame[:, :, 2] = (mask > 0) * 255 + (mask == 0) * frame[:, :, 2]

      # After locationg the current state of teh tracker, fund the location, and add a box around the object being tracked
      location = state['ploygon'].flatten() # Location to put box
      cv2.polylines(frame, [np.int0(location).reshape((-1, 1, 2))], True, (0, 255, 0), 3)
    
      # Write MODIFIEd frames into a new video file
      video_writer.write(frame)
  
    idx += 1
  video_test.release()
  video_writer.release()
  
  # convert the AVI file to MP4 video
  !ffmpeg -y -loglevel info -i outputVideo.avi output.mp4
else:
  print("can't open the given input video file!")

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3328: UserWarning: nn.functional.upsample is deprecated. Use nn.functional.interpolate instead.
  warnings.warn("nn.functional.upsample is deprecated. Use nn.functional.interpolate instead.")


ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

## Displaying the results of the SiamMask tracker on recycling data

In [9]:
# Displaying video on python notebook
def show_video_demo(file_name, width=640, height=480):
  video_encoded = base64.b64encode(io.open(file_name, 'rb').read())
  return HTML(data='''<video width="{0}" height="{1}" alt="test" controls>
                        <source src="data:video/mp4;base64,{2}" type="video/mp4" />
                      </video>'''.format(width, height, video_encoded.decode('ascii')))

# Run function to display video on Colab
show_video_demo('output.mp4', width=960, height=720)